In [13]:
# Import needed libraries 

import pandas as pd 
import os
import datetime
from datetime import timedelta
import numpy as np 
from scipy.signal import argrelextrema
import alpaca_trade_api as tradeapi 
import matplotlib.pyplot as plt 
import matplotlib.dates as mpdates
from mplfinance.original_flavor import candlestick_ohlc
from dotenv import load_dotenv
from itertools import islice
import hvplot.pandas

In [14]:
# Load .env file

load_dotenv()

True

In [15]:
# Set Alpaca API key and secret passwords

alpaca_api_key = os.getenv("ALPACA_API_KEY")
alpaca_secret_key = os.getenv("ALPACA_SECRET_KEY")

In [16]:
# Initiate REST API

api = tradeapi.REST(
    alpaca_api_key,
    alpaca_secret_key,
    api_version = "v2"
)

In [17]:
# Parameters for Stock Data from Alpacas
# Establish time frame (5 minute)

time_frame = "5min"

# Identify what stock symbol is trading

stock_symbol = "QQQ"

# Identify what start date to begin data analysis

start_date = pd.Timestamp("2021-02-01", tz="America/New_York").isoformat()

# Identify what end date to finalize data analysis

end_date = pd.Timestamp("2021-06-01", tz="America/New_York").isoformat()

In [18]:
# Function to call daily stock data

def get_stock_data(api, stock_symbol, time_frame, current_date_iso, next_day_date_iso):
    
    # Assuming api.get_bars returns a DataFrame with a 'df' attribute
    
    stock_data = api.get_bars(
        stock_symbol, 
        time_frame, 
        start=current_date_iso, 
        end=next_day_date_iso
        ).df
    
    return stock_data

# Displays the information pulled for working through code

# stock_data = get_stock_data(api, stock_symbol, time_frame, start_date, end_date)
# stock_data.info()
# display(stock_data.head())
# display(stock_data.tail())


In [19]:
# Function to prepare daily stock data to identify double top/bottom patterns and prepare for targets
# Includes establishing a polynomial fit and assigning new columns for localized min/max

# Polynomial Degree

polynomial_degree = 25

def polynomial_min_max_fit(stock_data, polynomial_degree):
    
    min_length = len(stock_data.index)
    x_data = np.arange(min_length)

    # Polynomial fitting
    polynomial_coefficients_open = np.polyfit(x_data, stock_data['open'][:min_length], polynomial_degree)
    polynomial_coefficients_high = np.polyfit(x_data, stock_data['high'][:min_length], polynomial_degree)
    polynomial_coefficients_low = np.polyfit(x_data, stock_data['low'][:min_length], polynomial_degree)
    polynomial_coefficients_close = np.polyfit(x_data, stock_data['close'][:min_length], polynomial_degree)

    # Evaluate the polynomial fit for plotting
    y_polynomial_open = np.polyval(polynomial_coefficients_open, x_data)
    y_polynomial_high = np.polyval(polynomial_coefficients_high, x_data)
    y_polynomial_low = np.polyval(polynomial_coefficients_low, x_data)
    y_polynomial_close = np.polyval(polynomial_coefficients_close, x_data)

    # Identify local extrema for polynomial fit data (minima and maxima)
    local_poly_minima = argrelextrema(y_polynomial_close, np.less, order=5)[0]
    local_poly_maxima = argrelextrema(y_polynomial_close, np.greater, order=5)[0]

    # Convert the close price polynomial fit data into a dataframe
    # This is done for OHLC poly fit data

    poly_df = pd.DataFrame(y_polynomial_open)
    columns = ['poly_fit_open']
    poly_df.columns = columns
    poly_df = poly_df.assign(poly_fit_high = y_polynomial_high)
    poly_df = poly_df.assign(poly_fit_low = y_polynomial_low)
    poly_df = poly_df.assign(poly_fit_close = y_polynomial_close)

    # Reset the index of the original updated ticker dataframe to concat with the polynomial dataframe that does not include a timeseries
    # This will ensure that the indexed intergers of the ploynomial fit align with the time each data point corresponds to

    updated_stock_data = stock_data.reset_index()
    updated_stock_data = pd.concat([updated_stock_data, poly_df], axis='columns', join='inner')
    updated_stock_data.head()

    # Add minima and maxima column to the DataFrame

    updated_stock_data["minima"] = 0
    updated_stock_data["maxima"] = 0
    updated_stock_data.head()

    # Mark rows with local minima as 1 in the 'minima' column

    for index in local_poly_minima:
        updated_stock_data.at[index, 'minima'] = -1

    for index in local_poly_maxima:
        updated_stock_data.at[index, "maxima"] = 1

    # Create Target Columns - Double Top Target & Double Bottom Target
        
    updated_stock_data["dbl_top_target"] = 0
    updated_stock_data["dbl_bot_target"] = 0

    # Create Machine Learning Model Target Column (Identify Long (1) or Short (-1))

    updated_stock_data["long_short_target"] = 0

    # # Plot data: COMMENTED OUT TO NOT REPEAT PLOTS AT END OF PROGRAM
    # # Plot the stock data and identified minima

    # plt.figure(figsize=(15, 5))
    # plt.plot(stock_data.index, stock_data["close"], label='Close Prices', alpha=0.7)

    # # Plot polynomial fit

    # plt.plot(stock_data.index[:min_length], y_polynomial_close, '-', markersize=1.0, color='black', alpha=0.9, label='Polynomial Fit')

    # # Plot red dots at local minima and blue dots at local maxima

    # plt.scatter(stock_data.index[local_poly_minima], y_polynomial_close[local_poly_minima], color='red', label='Local Minima')
    # plt.scatter(stock_data.index[local_poly_maxima],y_polynomial_close[local_poly_maxima], color="blue", label = "Local Maxima")
    
    return updated_stock_data

# For data checking/confirmation

# updated_stock_data = polynomial_min_max_fit(stock_data,polynomial_degree)

In [20]:
# # Plot data
# # Plot the stock data and identified minima

# plt.figure(figsize=(15, 5))
# plt.plot(stock_data.index, stock_data["close"], label='Close Prices', alpha=0.7)

# # # Plot polynomial fit

# plt.plot(stock_data.index[:min_length], y_polynomial_close, '-', markersize=1.0, color='black', alpha=0.9, label='Polynomial Fit')

# # # Plot red dots at local minima and blue dots at local maxima

# plt.scatter(stock_data.index[local_poly_minima], y_polynomial_close[local_poly_minima], color='red', label='Local Minima')
# plt.scatter(stock_data.index[local_poly_maxima],y_polynomial_close[local_poly_maxima], color="blue", label = "Local Maxima")

In [21]:
# Define the time independent DF for double top/bottom identification
# Timestamp remains a column, but can identify pattern from peak to peak immediately

def time_independent_data(updated_stock_data):

    # Define and establish time independent DF

    time_independent_df = []
    time_independent_df = pd.DataFrame(time_independent_df, columns = ["timestamp","close","high","low","trade_count","open","volume","vwap","poly_fit_open","poly_fit_high","poly_fit_low","poly_fit_close","minima","maxima","dbl_top_target","dbl_bot_target"])

    # Loop to iterate through all rows of stock data and write min/max to new DF

    for index, row in islice(updated_stock_data.iterrows(), 0, None):

        # Assign to rows only those that contain local min or max

        if (updated_stock_data.at[index,"minima"] == -1):
            time_independent_df.loc[index] = row
            a = updated_stock_data.iloc[index]["poly_fit_close"]
        elif (updated_stock_data.at[index,"maxima"] == 1):
            time_independent_df.loc[index] = row
            a = updated_stock_data.iloc[index]["poly_fit_close"]

    # Reset time dependent index
    # Set new time independent index

    time_independent_df.reset_index(inplace = True)
    time_independent_df.rename(columns={"index":"time_dependent_index"}, inplace = True)

    return time_independent_df

# Data confirmation/check

# time_independent_df = time_independent_data(updated_stock_data)
# time_independent_df.head(10)

In [22]:
# Function to identify daily double top/bottom patterns
# Inherently there should only be 1 identification of the pattern as it is considered a trend reversal pattern
# The loop will break once the pattern is identified

def identify_double_patterns(time_independent_df, updated_stock_data):

    # Initialize variables to identify double top/bottom patterns
    # Time dependent variable x_0 will always begin at a local min/max which also coincides
    # With the start of a trend into a potential double top/bottom
    
    x_0 = 0

    # Initiation of double top/bottom variable
    
    a = 0

    # First peak/valley of double top/bottom pattern
    
    b = 0

    # Trough/peak of double top/bottom pattern

    c = 0

    # Second peak/vallye of double top/bottom pattern
    
    d = 0

    # Trigger of double top/bottom pattern
    
    e = 0

    # Final time increment to finalize and trigger double top signal
    
    x_f = 0

    # Read through code to identify double top/bottom and assign to target columns.

    for index, row in islice(time_independent_df.iterrows(), 0, len(time_independent_df) - 4):

        # Check for double top
        # If found then assigns x_f final time for writing to targets in time dependent dataframe

        if (time_independent_df.at[index,"minima"] == -1):
            a = time_independent_df.iloc[index]["poly_fit_close"]
            b = time_independent_df.iloc[index + 1]["poly_fit_close"]
            c = time_independent_df.iloc[index + 2]["poly_fit_close"]
            d = time_independent_df.iloc[index + 3]["poly_fit_close"]
            e = time_independent_df.iloc[index + 4]["poly_fit_close"]
            x_0 = time_independent_df.iloc[index]["time_dependent_index"]

            if (time_independent_df.iloc[index + 1]["poly_fit_low"])*.95 < d < (time_independent_df.iloc[index + 1]["poly_fit_high"])*1.05 and (e <= c):
                x_f = time_independent_df.iloc[index + 4]["time_dependent_index"]
                updated_stock_data.at[x_f, "long_short_target"] = -1
                while (x_0 < x_f + 1):
                    updated_stock_data.at[x_0, "dbl_top_target"] = 1
                    x_0 = x_0 + 1
                break
            
            

        # Check for double bottom
        # If found then assigns x_f final time for writing to targets in time dependent dataframe
            
        elif (time_independent_df.at[index,"maxima"] == 1):
            a = time_independent_df.iloc[index]["poly_fit_close"]
            b = time_independent_df.iloc[index + 1]["poly_fit_close"]
            c = time_independent_df.iloc[index + 2]["poly_fit_close"]
            d = time_independent_df.iloc[index + 3]["poly_fit_close"]
            e = time_independent_df.iloc[index + 4]["poly_fit_close"]
            x_0 = time_independent_df.iloc[index]["time_dependent_index"] 

            if (time_independent_df.iloc[index+1]["poly_fit_low"])*.95 < d < (time_independent_df.iloc[index+1]["poly_fit_high"])*1.05 and (e >= c):
                x_f_min = time_independent_df.iloc[index + 4]["time_dependent_index"]
                updated_stock_data.at[x_f, "long_short_target"] = 1
                while (x_0 < x_f + 1):
                    updated_stock_data.at[x_0, "dbl_bot_target"] = 1
                    x_0 = x_0 + 1
                break
            
    return updated_stock_data, x_f

# updated_stock_data, x_f = identify_double_patterns(time_independent_df,updated_stock_data)

# print(x_f)



In [23]:
# # Data Checking

# display(updated_stock_data.head(20))
# print(updated_stock_data.loc[x_f])

In [24]:
# Loop to collect and assess daily data one day at a time

master_df = {
    'timestamp': [],  # List of timestamps
    'close': [],      # List of close prices
    'high': [],       # List of high prices
    'low': [],        # List of low prices
    'trade_count': [], # List of trade counts
    'open': [],       # List of open prices
    'volume': [],     # List of volumes
    'vwap': [],       # List of volume-weighted average prices
    'poly_fit_open': [],    # List of polynomial fit open prices
    'poly_fit_high': [],    # List of polynomial fit high prices
    'poly_fit_low': [],     # List of polynomial fit low prices
    'poly_fit_close': [],   # List of polynomial fit close prices
    'minima': [],           # List of minima
    'maxima': [],           # List of maxima
    'dbl_top_target': [],   # List of double top targets
    'dbl_bot_target': [],    # List of double bottom targets
    'buy_sell_tgt': []       # List of ML Model target
}

daily_dataframes = []

master_df = pd.DataFrame(master_df)

current_date = pd.to_datetime(start_date)
next_day_date = current_date + pd.offsets.BDay(1)

print(current_date)
print(next_day_date)

while current_date <= (pd.to_datetime(end_date)):

    # next_day_date = next_day_date + pd.offsets.BDay(1)
    # current_date = current_date + pd.offsets.BDay(1)
    # Convert current_date and next_day_date to ISO format for API call

    current_date_iso = current_date.isoformat()
    # next_day_date = current_date + pd.offsets.BDay(1)
    next_day_date_iso = next_day_date.isoformat()

    #current_date = datetime.datetime.fromisoformat(current_date_iso) + pd.offsets.BDay(1)
    
    # Fetch stock data for the current day

    stock_data = get_stock_data(api, stock_symbol, time_frame, current_date_iso, next_day_date_iso)

    if len(stock_data.index) == 0:
        next_day_date = next_day_date + pd.offsets.BDay(1)
        current_date = current_date + pd.offsets.BDay(1)
        continue
    
    # Run polynomial fit function for updated stock data

    updated_stock_data = polynomial_min_max_fit(stock_data, polynomial_degree)
    
    # Isolate Mins/maxes

    time_independent_df = time_independent_data(updated_stock_data)

    # Updated stock data with double tops/bots identified by function
    # x_f is the double top/bot trigger row(index) for current day's double top/bot

    updated_stock_data, x_f = identify_double_patterns(time_independent_df, updated_stock_data)
    
    # Perform your analysis or call your functions here
    # e.g., identify_double_patterns(time_independent_df, updated_stock_data)

    daily_dataframes.append(updated_stock_data)

    master_df = pd.concat(daily_dataframes, ignore_index=True)
    # display(master_df.tail())
    # Increment to the next day

    next_day_date = next_day_date + pd.offsets.BDay(1)
    current_date = current_date + pd.offsets.BDay(1)
    # next_day_date = pd.Timestamp(next_day_date_iso) + pd.offsets.BDay(1)
    
    # print(current_date)
    # print(next_day_date)
    


2021-02-01 00:00:00-05:00
2021-02-02 00:00:00-05:00


/var/folders/sr/78cv2dx14kgdcwtf90634z580000gn/T/ipykernel_10213/2973665038.py:14: RankWarning: Polyfit may be poorly conditioned
  polynomial_coefficients_open = np.polyfit(x_data, stock_data['open'][:min_length], polynomial_degree)
/var/folders/sr/78cv2dx14kgdcwtf90634z580000gn/T/ipykernel_10213/2973665038.py:15: RankWarning: Polyfit may be poorly conditioned
  polynomial_coefficients_high = np.polyfit(x_data, stock_data['high'][:min_length], polynomial_degree)
/var/folders/sr/78cv2dx14kgdcwtf90634z580000gn/T/ipykernel_10213/2973665038.py:16: RankWarning: Polyfit may be poorly conditioned
  polynomial_coefficients_low = np.polyfit(x_data, stock_data['low'][:min_length], polynomial_degree)
/var/folders/sr/78cv2dx14kgdcwtf90634z580000gn/T/ipykernel_10213/2973665038.py:17: RankWarning: Polyfit may be poorly conditioned
  polynomial_coefficients_close = np.polyfit(x_data, stock_data['close'][:min_length], polynomial_degree)
/var/folders/sr/78cv2dx14kgdcwtf90634z580000gn/T/ipykernel_10213

In [28]:
master_df.info()
print(len(master_df))
print(type(master_df))
print(sum(master_df["dbl_top_target"]))
print(sum(master_df["dbl_bot_target"]))
print(sum(master_df["long_short_target"]))
display(master_df.head(50))
display(master_df.tail(50))

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 15458 entries, 0 to 15457
Data columns (total 17 columns):
 #   Column             Non-Null Count  Dtype              
---  ------             --------------  -----              
 0   timestamp          15458 non-null  datetime64[ns, UTC]
 1   close              15458 non-null  float64            
 2   high               15458 non-null  float64            
 3   low                15458 non-null  float64            
 4   trade_count        15458 non-null  int64              
 5   open               15458 non-null  float64            
 6   volume             15458 non-null  int64              
 7   vwap               15458 non-null  float64            
 8   poly_fit_open      15458 non-null  float64            
 9   poly_fit_high      15458 non-null  float64            
 10  poly_fit_low       15458 non-null  float64            
 11  poly_fit_close     15458 non-null  float64            
 12  minima             15458 non-null  int64      

timestamp   close      high      low  trade_count  \
0  2021-02-01 09:00:00+00:00  317.78  317.7900  317.260          457   
1  2021-02-01 09:05:00+00:00  317.63  317.7900  317.540           42   
2  2021-02-01 09:10:00+00:00  317.85  317.9000  317.650           41   
3  2021-02-01 09:15:00+00:00  318.15  318.2500  317.970           77   
4  2021-02-01 09:20:00+00:00  318.01  318.3300  318.000           88   
5  2021-02-01 09:25:00+00:00  318.11  318.1600  318.000           42   
6  2021-02-01 09:30:00+00:00  318.06  318.1700  318.060          157   
7  2021-02-01 09:35:00+00:00  317.84  318.0800  317.810           32   
8  2021-02-01 09:40:00+00:00  317.71  317.9100  317.700           61   
9  2021-02-01 09:45:00+00:00  317.49  317.8100  317.490           25   
10 2021-02-01 09:50:00+00:00  317.54  317.8100  317.540           16   
11 2021-02-01 09:55:00+00:00  317.94  318.0000  317.770           38   
12 2021-02-01 10:00:00+00:00  318.06  318.1600  317.980           45   
13 2021-02-01 10:05:00+00:00  318.08  318.0800  317.900           32   
14 2021-02-01 10:10:00+00:00  317.99  318.2300  317.990           36   
15 2021-02-01 10:15:00+00:00  317.88  318.1700  317.880           45   
16 2021-02-01 10:20:00+00:00  317.89  318.0700  317.890           35   
17 2021-02-01 10:25:00+00:00  317.90  317.9600  317.770           47   
18 2021-02-01 10:30:00+00:00  317.66  317.9300  317.660           27   
19 2021-02-01 10:35:00+00:00  317.83  317.8300  317.710           12   
20 2021-02-01 10:40:00+00:00  317.59  318.2200  317.480           42   
21 2021-02-01 10:45:00+00:00  317.82  317.8200  317.680            9   
22 2021-02-01 10:50:00+00:00  317.72  317.9100  317.720           10   
23 2021-02-01 10:55:00+00:00  317.57  317.6700  317.570           21   
24 2021-02-01 11:00:00+00:00  317.61  317.6600  317.610            5   
25 2021-02-01 11:05:00+00:00  317.76  317.7600  317.560            9   
26 2021-02-01 11:10:00+00:00  317.75  317.7700  317.560           13   
27 2021-02-01 11:15:00+00:00  317.90  318.0500  317.900           21   
28 2021-02-01 11:20:00+00:00  318.22  318.3300  317.910           43   
29 2021-02-01 11:25:00+00:00  318.69  318.7500  318.170           59   
30 2021-02-01 11:30:00+00:00  318.50  318.7700  318.500           22   
31 2021-02-01 11:35:00+00:00  318.19  318.3500  318.190           43   
32 2021-02-01 11:40:00+00:00  318.00  318.2400  318.000           46   
33 2021-02-01 11:45:00+00:00  317.89  318.0300  317.830           60   
34 2021-02-01 11:50:00+00:00  318.28  318.2900  317.910           22   
35 2021-02-01 11:55:00+00:00  317.88  318.0400  317.880           88   
36 2021-02-01 12:00:00+00:00  317.77  317.9800  317.630          300   
37 2021-02-01 12:05:00+00:00  317.68  318.0100  317.670          267   
38 2021-02-01 12:10:00+00:00  317.84  317.9100  317.650           84   
39 2021-02-01 12:15:00+00:00  318.15  318.2500  317.909          134   
40 2021-02-01 12:20:00+00:00  318.19  318.3100  318.190           87   
41 2021-02-01 12:25:00+00:00  318.24  318.3300  318.140          117   
42 2021-02-01 12:30:00+00:00  318.13  318.3800  318.130          186   
43 2021-02-01 12:35:00+00:00  318.28  318.2900  318.000          112   
44 2021-02-01 12:40:00+00:00  318.55  318.6200  318.280          112   
45 2021-02-01 12:45:00+00:00  318.35  318.5400  318.330           65   
46 2021-02-01 12:50:00+00:00  318.38  318.5100  318.300           93   
47 2021-02-01 12:55:00+00:00  317.98  318.4000  317.980          173   
48 2021-02-01 13:00:00+00:00  315.33  318.7796  315.330          516   
49 2021-02-01 13:05:00+00:00  318.14  318.1400  317.960          108   

        open  volume        vwap  poly_fit_open  poly_fit_high  poly_fit_low  \
0   317.6200  152785  317.615546     317.589182     317.713881    317.194753   
1   317.7500    5968  317.621602     317.741116     317.920431    317.621392   
2   317.6500    5138  317.836724     317.855104     318.045421    317.816207   
3   318.0000   18913  318.

timestamp     close      high       low  trade_count  \
15408 2021-05-28 17:35:00+00:00  334.5300  334.8700  334.4800         1967   
15409 2021-05-28 17:40:00+00:00  334.4800  334.5650  334.3800         1885   
15410 2021-05-28 17:45:00+00:00  334.3000  334.5000  334.1800         2514   
15411 2021-05-28 17:50:00+00:00  334.4600  334.4600  334.2500         1445   
15412 2021-05-28 17:55:00+00:00  334.4300  334.4900  334.3200         1317   
15413 2021-05-28 18:00:00+00:00  334.4799  334.4806  334.3400         1920   
15414 2021-05-28 18:05:00+00:00  334.3900  334.5400  334.3300         1981   
15415 2021-05-28 18:10:00+00:00  334.3399  334.4300  334.2100         2164   
15416 2021-05-28 18:15:00+00:00  334.4130  334.4700  334.2700         1787   
15417 2021-05-28 18:20:00+00:00  334.4799  334.4900  334.3200         1839   
15418 2021-05-28 18:25:00+00:00  334.7200  334.7200  334.4350         1812   
15419 2021-05-28 18:30:00+00:00  334.7199  334.7290  334.5850         1881   
15420 2021-05-28 18:35:00+00:00  334.6900  334.7500  334.6300         1656   
15421 2021-05-28 18:40:00+00:00  334.8100  334.8301  334.6700         1875   
15422 2021-05-28 18:45:00+00:00  334.8800  334.9100  334.8000          953   
15423 2021-05-28 18:50:00+00:00  334.8800  334.9600  334.8100         1491   
15424 2021-05-28 18:55:00+00:00  334.7850  334.9100  334.7250         1738   
15425 2021-05-28 19:00:00+00:00  334.7518  334.8100  334.6100         1784   
15426 2021-05-28 19:05:00+00:00  334.6791  334.7700  334.6360         1164   
15427 2021-05-28 19:10:00+00:00  334.4318  334.6800  334.3300         2578   
15428 2021-05-28 19:15:00+00:00  334.5500  334.5800  334.3800         2363   
15429 2021-05-28 19:20:00+00:00  334.4950  334.5900  334.4600         1749   
15430 2021-05-28 19:25:00+00:00  334.5900  334.6500  334.3600         1750   
15431 2021-05-28 19:30:00+00:00  334.4650  334.6400  334.4400         2351   
15432 2021-05-28 19:35:00+00:00  334.6100  334.7600  334.4500         2371   
15433 2021-05-28 19:40:00+00:00  334.3884  334.6000  334.3400         2575   
15434 2021-05-28 19:45:00+00:00  334.4200  334.5600  334.3582         3252   
15435 2021-05-28 19:50:00+00:00  333.8850  334.5000  333.6800         8652   
15436 2021-05-28 19:55:00+00:00  333.7900  333.9300  333.6000        15424   
15437 2021-05-28 20:00:00+00:00  333.8600  333.9900  333.7800          919   
15438 2021-05-28 20:05:00+00:00  333.8600  333.9300  333.8200          359   
15439 2021-05-28 20:10:00+00:00  333.8400  333.9300  333.7800          327   
15440 2021-05-28 20:15:00+00:00  333.7800  333.9000  333.6130          115   
15441 2021-05-28 20:20:00+00:00  333.8200  333.8200  333.7500           41   
15442 2021-05-28 20:25:00+00:00  333.9100  333.9100  333.8200           73   
15443 2021-05-28 20:30:00+00:00  333.8000  333.9300  332.9169          109   
15444 2021-05-28 20:35:00+00:00  333.7900  333.8400  333.7900           18   
15445 2021-05-28 20:40:00+00:00  333.7500  333.8100  333.7200          123   
15446 2021-05-28 20:45:00+00:00  333.8000  333.8000  333.7500           30   
15447 2021-05-28 20:50:00+00:00  333.7400  333.8000  333.7300           39   
15448 2021-05-28 20:55:00+00:00  333.7300  333.7600  333.7200           47   
15449 2021-05-28 21:00:00+00:00  333.8100  333.8100  333.7000           10   
15450 2021-05-28 21:05:00+00:00  333.7800  333.8100  333.7800            4   
15451 2021-05-28 21:15:00+00:00  333.8000  333.8000  333.8000            6   
15452 2021-05-28 21:20:00+00:00  333.8400  333.8400  333.7800           15   
15453 2021-05-28 21:25:00+00:00  333.8400  333.8400  333.8000           12   
15454 2021-05-28 21:30:00+00:00  333.8000  333.8200  333.8000           15   
15455 2021-05-28 21:45:00+00:00  333.8400  333.8400  333.8200           11   
15456 2021-05-28 21:50:00+00:00  333.8300  333.8300  333.8200            6   
15457 2021-05-28 21:55:00+00:00  333.8200  333.8300  333.8200           11   

           open   volume        vwap  poly_

In [26]:
print(current_date)

2021-06-01 00:00:00-05:00


In [27]:
master_df.hvplot(x = "timestamp")



/Users/ebrown/anaconda3/envs/machine_learning/lib/python3.10/site-packages/holoviews/core/data/pandas.py:39: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  return dataset.data.dtypes[idx].type
/Users/ebrown/anaconda3/envs/machine_learning/lib/python3.10/site-packages/holoviews/core/data/pandas.py:39: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  return dataset.data.dtypes[idx].type
/Users/ebrown/anaconda3/envs/machine_learning/lib/python3.10/site-packages/holoviews/core/data/pandas.py:362: FutureWarning: The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series conta

:NdOverlay   [Variable]
   :Curve   [timestamp]   (value)